# How to create a trading bot in Python (2) - for beginners, using RSI, TA-lib, Alpaca, Anaconda.

If you want, you can find the previous tutorial about starting with Anaconda, Alpaca, Jupyter Notebook, and creating a simple trading bot in 10 lines of code at: 

https://superai.pl/the_simple_trading_bot.html

### The trading bot using Relative Strength Index to decide when to buy or sell  shares in less than 15 lines of code

Specification of the bot below (things you might modify are bolded):
- buys **10** shares of **AAPL** when the RSI (from last **3** close prices measured in 1 minute intervals) is less than **49** and you have no shares in your protfolio
- sells **10** shares of **AAPL** when the RSI (from last **3** close prices measured in 1 minute intervals) is more than **51** and you have some shares in your portfolio

In [ ]:
import alpaca_trade_api as tradeapi, ast, json, numpy as np, talib as ta, websocket
data = []
def on_open(ws):
    ws.send(json.dumps({"action": "authenticate", "data": {"key_id": "paste your KEY_ID here", "secret_key": "paste your SECRET_KEY here"}}))
    ws.send(json.dumps({"action": "listen", "data": {"streams": ["AM.AAPL"]}}))
def on_message(ws, message):
    if isinstance(ast.literal_eval(message).get("data").get("c"), float): data.append(ast.literal_eval(message).get("data").get("c"))        
    if len(data) > 3 and ta.RSI(np.array(data), 3)[-1] < 49:
        try: tradeapi.REST("paste your KEY_ID here", "paste your SECRET_KEY here", "https://paper-api.alpaca.markets", "v2").get_position("AAPL")
        except:tradeapi.REST("paste your KEY_ID here", "paste your SECRET_KEY here", "https://paper-api.alpaca.markets", "v2").submit_order(symbol="AAPL", qty=10, side = "buy", type='market', time_in_force='gtc')            
    elif len(data) > 3 and ta.RSI(np.array(data), 3)[-1] > 51:
        tradeapi.REST("paste your KEY_ID here", "paste your SECRET_KEY here", "https://paper-api.alpaca.markets", "v2").get_position("AAPL")
        tradeapi.REST("paste your KEY_ID here", "paste your SECRET_KEY here", "https://paper-api.alpaca.markets", "v2").submit_order(symbol="AAPL",qty=10,side='sell',type='market',time_in_force='gtc')
websocket.WebSocketApp("wss://data.alpaca.markets/stream", on_open=on_open, on_message=on_message).run_forever()